In [1]:
import random as rd
import pandas as pd
import math
import numpy as np
import random

from itertools import chain, combinations

In [2]:
masterTable = pd.read_csv('data.csv')

In [3]:
masterTable.head()

Elevation  Aspect  Slope  Horizontal_Distance_To_Hydrology  \
0       2596      51      3                               258   
1       2590      56      2                               212   
2       2804     139      9                               268   
3       2785     155     18                               242   
4       2595      45      2                               153   

   Vertical_Distance_To_Hydrology  Horizontal_Distance_To_Roadways  \
0                               0                              510   
1                              -6                              390   
2                              65                             3180   
3                             118                             3090   
4                              -1                              391   

   Hillshade_9am  Hillshade_Noon  Hillshade_3pm  \
0            221             232            148   
1            220             235            151   
2            234             238            135   
3            238             238            122   
4            220             234            150   

   Horizontal_Distance_To_Fire_Points  ...  Soil_Type35  Soil_Type36  \
0                                6279  ...            0            0   
1                                6225  ...            0            0   
2                                6121  ...            0            0   
3                                6211  ...            0            0   
4                                6172  ...            0            0   

   Soil_Type37  Soil_Type38  Soil_Type39  Soil_Type40  Cover_Type  Unknown 1  \
0            0            0            0            0           0          0   
1            0            0            0            0           0          0   
2            0            0            0            0           0          0   
3            0            0            0            0           0          0   
4            0            0            0            0           0          0   

   Unknown 2  Unknown 3  
0          0          5  
1          0          5  
2          0          2  
3          0          2  
4          0          5  

[5 rows x 55 columns]

In [4]:
dataset = masterTable.iloc[: , :10]

In [5]:
dataset.head()

Elevation  Aspect  Slope  Horizontal_Distance_To_Hydrology  \
0       2596      51      3                               258   
1       2590      56      2                               212   
2       2804     139      9                               268   
3       2785     155     18                               242   
4       2595      45      2                               153   

   Vertical_Distance_To_Hydrology  Horizontal_Distance_To_Roadways  \
0                               0                              510   
1                              -6                              390   
2                              65                             3180   
3                             118                             3090   
4                              -1                              391   

   Hillshade_9am  Hillshade_Noon  Hillshade_3pm  \
0            221             232            148   
1            220             235            151   
2            234             238            135   
3            238             238            122   
4            220             234            150   

   Horizontal_Distance_To_Fire_Points  
0                                6279  
1                                6225  
2                                6121  
3                                6211  
4                                6172

In [6]:
def generate_subsets(arr):
    all_subsets = []
    for r in range(1, len(arr) + 1):
        subsets_r = list(combinations(arr, r))
        all_subsets.extend(subsets_r)

    return [list(subset) for subset in all_subsets]

In [7]:
def genr_data_distr(col,count):
  l_data = []
  col =  col.to_list()
  for i in range(count):
    index = rd.choice(col)
    l_data.append([index])
  return l_data

In [8]:
def getRanges(cols, noSamplesSet):
  attToDist = dict()
  for c in cols:
    attToDist[c] = genr_data_distr(dataset[c], noSamplesSet)
  return attToDist

In [9]:
def create_zero_dataframe(n, D):
    data = {f"Attribute_{i}": [0] * n for i in range(1, D+1)}
    df = pd.DataFrame(data)
    return df

def generateSkeletonData(n, columns):
  zero_df = create_zero_dataframe(n, 4*len(columns))
  newColNames =[]
  for c in columns:
    newColNames.append(c + " <")
    newColNames.append(c + " =")
    newColNames.append(c + " >")
    newColNames.append(c + " values")
  zero_df.columns = newColNames
  return zero_df

In [10]:
def findIndex(col, columns):
  for i,c in enumerate(columns):
    if (c == col):
      return i

In [11]:
def generate_random_ohe(n):
    possibilities = [[1, 1, 0], [0, 1, 1], [1, 0, 0], [0, 1, 0], [0, 0, 1]]
    samples = []
    for _ in range(n):
        sample = random.choice(possibilities)
        samples.append(sample)
    return samples


In [12]:
n = 20000
columns = list(dataset.columns)
subsets = generate_subsets(columns)

sampleSize = math.ceil(n/len(subsets))
distributions = getRanges(columns, sampleSize)
data = generateSkeletonData(sampleSize*len(subsets), columns)
ctr = 0
for s in subsets:
  for c in s:
    index = findIndex(c, columns)
    randoperators = generate_random_ohe(sampleSize)
    data.iloc[ctr : ctr+sampleSize, 4*index +3 : 4*index+4] = distributions[c]
    data.iloc[ctr : ctr+sampleSize, 4*index : 4*index+3] = randoperators
  ctr = ctr + sampleSize


In [13]:
data.shape

(20460, 40)

In [14]:
pd.set_option('display.max_columns', None)
data

Elevation <  Elevation =  Elevation >  Elevation values  Aspect <  \
0                0            0            1              2954         0   
1                0            1            0              3031         0   
2                0            1            0              3380         0   
3                0            1            1              2905         0   
4                1            1            0              2919         0   
...            ...          ...          ...               ...       ...   
20455            0            1            0              2540         0   
20456            1            1            0              3118         0   
20457            0            1            1              2584         1   
20458            0            1            1              2893         0   
20459            0            1            0              2901         1   

       Aspect =  Aspect >  Aspect values  Slope <  Slope =  Slope >  \
0             0         0              0        0        0        0   
1             0         0              0        0        0        0   
2             0         0              0        0        0        0   
3             0         0              0        0        0        0   
4             0         0              0        0        0        0   
...         ...       ...            ...      ...      ...      ...   
20455         1         0             34        0        1        0   
20456         0         1             56        0        0        1   
20457         0         0             87        0        1        1   
20458         1         0            150        1        0        0   
20459         1         0             12        0        1        1   

       Slope values  Horizontal_Distance_To_Hydrology <  \
0                 0                                   0   
1                 0                                   0   
2                 0                                   0   
3                 0                                   0   
4                 0                                   0   
...             ...                                 ...   
20455            12                                   0   
20456             9                                   0   
20457            10                                   1   
20458            14                                   0   
20459             5                                   1   

       Horizontal_Distance_To_Hydrology =  Horizontal_Distance_To_Hydrology >  \
0                                       0                                   0   
1                                       0                                   0   
2                                       0                                   0   
3                                       0                                   0   
4                                       0                                   0   
...                                   ...                                 ...   
20455                                   1                                   1   
20456                                   1                                   0   
20457                                   0                                   0   
20458                                   1                                   0   
20459                                   0                                   0   

       Horizontal_Distance_To_Hydrology values  \
0                                            0   
1                                            0   
2                                            0   
3                                            0   
4                                            0   
...                                        ...   
20455                                       90   
20456                                      108   
20457                                      666   
20458                                      382   
20459    

In [15]:
# row_data = data.loc[20459]
# for column, value in row_data.iteritems():
#     print(f'{column}: {value}')

# print(data.columns)


In [16]:
data.to_csv('LM_Data.csv', index=False)

In [17]:
!pip install pandas mysql-connector-python

In [18]:
import mysql.connector
from mysql.connector import Error

In [19]:
try:
        connection = mysql.connector.connect(
                                         host='localhost',
                                         database='dbms',
                                         user='root',
                                         password='Tol@sql')
        if connection.is_connected():
            db_Info = connection.get_server_info()
            print("Connected to MySQL Server version ", db_Info)
            cursor = connection.cursor()
            cursor.execute("select database();")
            record = cursor.fetchone()
            print("You're connected to database: ", record)

except Error as err:
        print("Error while connecting to MySQL", err)

Connected to MySQL Server version  8.0.36
You're connected to database:  ('dbms',)


In [20]:
connection

In [21]:
def read_query(connection, query):
    cursor = connection.cursor()
    try:
        cursor.execute(query)
        result = cursor.fetchall()
        return result
    except Error as err:
        print(f'Error: {err}')

In [22]:
cursor = connection.cursor()

In [23]:
# Function to get the total number of rows in DBMS.forest
def total_rows_count(connection):
    try:
        cursor = connection.cursor()
        cursor.execute("SELECT COUNT(*) FROM dbms.forest")
        total_rows = cursor.fetchone()[0]
        return total_rows
    except Error as err:
        print("Error fetching total rows from DBMS.forest", err)
        return None
    finally:
        cursor.close()

# Function to execute SQL queries and store results
def execute_sql_queries(df, connection):
    # First, get the total number of rows in DBMS.forest
    total_rows = total_rows_count(connection)
    if total_rows is None:  # Check if fetching total rows failed
        return pd.DataFrame()  # Return empty DataFrame if total row count couldn't be fetched

    results = []  # List to store the results of each query
#     for index, row in df.head(10).iterrows():
    for index, row in df.iterrows():
        condition_dict = {}
        for col in df.columns:
            if '<' in col or '=' in col or '>' in col:
                attr, op = col.rsplit(' ', 1)
                if row[col] == 1:
                    value_col = f"{attr} values"
                    value = row[value_col]
                    condition_str = f"{attr} {op} {value}"
                    if attr in condition_dict:
                        condition_dict[attr].append(condition_str)
                    else:
                        condition_dict[attr] = [condition_str]

        conditions = []
        for attr, cond_list in condition_dict.items():
            if len(cond_list) > 1:
                conditions.append(f"({' OR '.join(cond_list)})")
            else:
                conditions.append(cond_list[0])

        where_clause = ' AND '.join(conditions)
        sql_query = f"SELECT COUNT(*) FROM dbms.forest WHERE {where_clause}"

        # Execute the query and normalize the result
        try:
            cursor = connection.cursor()
            cursor.execute(sql_query)
            count_result = cursor.fetchone()[0]
            selectivity_result = count_result / total_rows if total_rows > 0 else None  # Avoid division by zero
            results.append(selectivity_result)
            print(f"sql_query: {sql_query} \n selectivity_result: {selectivity_result}\n\n")
        except Error as err:
            print("Error while executing query", err)
            results.append(None)
        finally:
            cursor.close()

    # Create a DataFrame from the normalized results
    check_df = pd.DataFrame({'Selectivity Result': results})
    return check_df

# Assuming 'data' is your DataFrame and 'connection' is your MySQL connection object
check_df = execute_sql_queries(data, connection)


print(check_df)


sql_query: SELECT COUNT(*) FROM dbms.forest WHERE Elevation > 2954 
 selectivity_result: 0.5727747447557021


sql_query: SELECT COUNT(*) FROM dbms.forest WHERE Elevation = 3031 
 selectivity_result: 0.0023837717637501463


sql_query: SELECT COUNT(*) FROM dbms.forest WHERE Elevation = 3380 
 selectivity_result: 0.00038381307098648567


sql_query: SELECT COUNT(*) FROM dbms.forest WHERE (Elevation = 2905 OR Elevation > 2905) 
 selectivity_result: 0.6480640675235624


sql_query: SELECT COUNT(*) FROM dbms.forest WHERE (Elevation < 2919 OR Elevation = 2919) 
 selectivity_result: 0.3730972854261186


sql_query: SELECT COUNT(*) FROM dbms.forest WHERE Elevation > 3047 
 selectivity_result: 0.4154423660784975


sql_query: SELECT COUNT(*) FROM dbms.forest WHERE Elevation > 2934 
 selectivity_result: 0.6052921454290101


sql_query: SELECT COUNT(*) FROM dbms.forest WHERE Elevation < 2791 
 selectivity_result: 0.23353390291422552


sql_query: SELECT COUNT(*) FROM dbms.forest WHERE (Elevation = 3322 

sql_query: SELECT COUNT(*) FROM dbms.forest WHERE Horizontal_Distance_To_Hydrology > 90 
 selectivity_result: 0.7716363861675835


sql_query: SELECT COUNT(*) FROM dbms.forest WHERE Horizontal_Distance_To_Hydrology = 150 
 selectivity_result: 0.035773787804726925


sql_query: SELECT COUNT(*) FROM dbms.forest WHERE (Horizontal_Distance_To_Hydrology < 95 OR Horizontal_Distance_To_Hydrology = 95) 
 selectivity_result: 0.244225592586728


sql_query: SELECT COUNT(*) FROM dbms.forest WHERE (Horizontal_Distance_To_Hydrology = 649 OR Horizontal_Distance_To_Hydrology > 649) 
 selectivity_result: 0.061050374174715843


sql_query: SELECT COUNT(*) FROM dbms.forest WHERE (Horizontal_Distance_To_Hydrology < 170 OR Horizontal_Distance_To_Hydrology = 170) 
 selectivity_result: 0.39420872546522273


sql_query: SELECT COUNT(*) FROM dbms.forest WHERE (Horizontal_Distance_To_Hydrology = 124 OR Horizontal_Distance_To_Hydrology > 124) 
 selectivity_result: 0.7126926810461746


sql_query: SELECT COUNT(*) FROM

sql_query: SELECT COUNT(*) FROM dbms.forest WHERE Hillshade_9am > 253 
 selectivity_result: 0.0032667139405038108


sql_query: SELECT COUNT(*) FROM dbms.forest WHERE (Hillshade_9am < 169 OR Hillshade_9am = 169) 
 selectivity_result: 0.07439261151232676


sql_query: SELECT COUNT(*) FROM dbms.forest WHERE (Hillshade_9am = 151 OR Hillshade_9am > 151) 
 selectivity_result: 0.967012729513332


sql_query: SELECT COUNT(*) FROM dbms.forest WHERE Hillshade_9am = 214 
 selectivity_result: 0.014447205909688612


sql_query: SELECT COUNT(*) FROM dbms.forest WHERE Hillshade_9am > 251 
 selectivity_result: 0.011526440073526881


sql_query: SELECT COUNT(*) FROM dbms.forest WHERE Hillshade_9am < 232 
 selectivity_result: 0.7527004605756852


sql_query: SELECT COUNT(*) FROM dbms.forest WHERE (Hillshade_9am < 182 OR Hillshade_9am = 182) 
 selectivity_result: 0.13058938541716866


sql_query: SELECT COUNT(*) FROM dbms.forest WHERE Hillshade_9am = 208 
 selectivity_result: 0.013249296055847383


sql_query: 

sql_query: SELECT COUNT(*) FROM dbms.forest WHERE (Horizontal_Distance_To_Fire_Points = 997 OR Horizontal_Distance_To_Fire_Points > 997) 
 selectivity_result: 0.7607054587512823


sql_query: SELECT COUNT(*) FROM dbms.forest WHERE (Horizontal_Distance_To_Fire_Points = 1595 OR Horizontal_Distance_To_Fire_Points > 1595) 
 selectivity_result: 0.539947539809849


sql_query: SELECT COUNT(*) FROM dbms.forest WHERE (Horizontal_Distance_To_Fire_Points = 258 OR Horizontal_Distance_To_Fire_Points > 258) 
 selectivity_result: 0.9801535940737885


sql_query: SELECT COUNT(*) FROM dbms.forest WHERE (Horizontal_Distance_To_Fire_Points < 631 OR Horizontal_Distance_To_Fire_Points = 631) 
 selectivity_result: 0.11183417898425506


sql_query: SELECT COUNT(*) FROM dbms.forest WHERE Horizontal_Distance_To_Fire_Points < 1842 
 selectivity_result: 0.5437323153394422


sql_query: SELECT COUNT(*) FROM dbms.forest WHERE Horizontal_Distance_To_Fire_Points < 1530 
 selectivity_result: 0.4361820409905475


sql_quer

sql_query: SELECT COUNT(*) FROM dbms.forest WHERE (Elevation = 2919 OR Elevation > 2919) AND (Horizontal_Distance_To_Hydrology < 573 OR Horizontal_Distance_To_Hydrology = 573) 
 selectivity_result: 0.5430283711868258


sql_query: SELECT COUNT(*) FROM dbms.forest WHERE Elevation = 3047 AND (Horizontal_Distance_To_Hydrology = 255 OR Horizontal_Distance_To_Hydrology > 255) 
 selectivity_result: 0.0011996309886887018


sql_query: SELECT COUNT(*) FROM dbms.forest WHERE Elevation = 2934 AND Horizontal_Distance_To_Hydrology > 85 
 selectivity_result: 0.0008932689858385024


sql_query: SELECT COUNT(*) FROM dbms.forest WHERE Elevation < 2791 AND Horizontal_Distance_To_Hydrology < 90 
 selectivity_result: 0.07102607175066952


sql_query: SELECT COUNT(*) FROM dbms.forest WHERE (Elevation = 3322 OR Elevation > 3322) AND (Horizontal_Distance_To_Hydrology = 90 OR Horizontal_Distance_To_Hydrology > 90) 
 selectivity_result: 0.0534395158791901


sql_query: SELECT COUNT(*) FROM dbms.forest WHERE (Eleva

...

sql_query: SELECT COUNT(*) FROM dbms.forest WHERE (Elevation < 2540 OR Elevation = 2540) AND (Aspect < 34 OR Aspect = 34) AND (Slope < 12 OR Slope = 12) AND (Vertical_Distance_To_Hydrology < -18 OR Vertical_Distance_To_Hydrology = -18) AND (Horizontal_Distance_To_Roadways < 3428 OR Horizontal_Distance_To_Roadways = 3428) AND Hillshade_9am > 134 AND Hillshade_Noon = 247 AND (Hillshade_3pm < 157 OR Hillshade_3pm = 157) AND (Horizontal_Distance_To_Fire_Points = 2314 OR Horizontal_Distance_To_Fire_Points > 2314) 
 selectivity_result: 0.0


sql_query: SELECT COUNT(*) FROM dbms.forest WHERE (Elevation = 3118 OR Elevation > 3118) AND (Aspect = 56 OR Aspect > 56) AND Slope > 9 AND Vertical_Distance_To_Hydrology = 31 AND (Horizontal_Distance_To_Roadways < 2258 OR Horizontal_Distance_To_Roadways = 2258) AND Hillshade_9am < 239 AND Hillshade_Noon < 228 AND Hillshade_3pm = 146 AND (Horizontal_Distance_To_Fire_Points < 3190 OR Horizontal_Distance_To_Fire_Points = 3190) 
 selectivity_result: 0.0


s

sql_query: SELECT COUNT(*) FROM dbms.forest WHERE (Elevation = 2946 OR Elevation > 2946) AND (Aspect < 309 OR Aspect = 309) AND Horizontal_Distance_To_Hydrology = 170 AND Vertical_Distance_To_Hydrology = -1 AND (Horizontal_Distance_To_Roadways < 5728 OR Horizontal_Distance_To_Roadways = 5728) AND Hillshade_9am = 202 AND Hillshade_Noon = 201 AND Hillshade_3pm < 139 AND (Horizontal_Distance_To_Fire_Points = 1842 OR Horizontal_Distance_To_Fire_Points > 1842) 
 selectivity_result: 0.0


sql_query: SELECT COUNT(*) FROM dbms.forest WHERE Elevation < 2908 AND Aspect < 340 AND Horizontal_Distance_To_Hydrology > 124 AND Vertical_Distance_To_Hydrology > 2 AND (Horizontal_Distance_To_Roadways < 2837 OR Horizontal_Distance_To_Roadways = 2837) AND Hillshade_9am > 176 AND (Hillshade_Noon = 232 OR Hillshade_Noon > 232) AND (Hillshade_3pm < 101 OR Hillshade_3pm = 101) AND (Horizontal_Distance_To_Fire_Points = 1530 OR Horizontal_Distance_To_Fire_Points > 1530) 
 selectivity_result: 0.0


sql_query: SEL

sql_query: SELECT COUNT(*) FROM dbms.forest WHERE Elevation > 2926 AND Slope = 5 AND Horizontal_Distance_To_Hydrology = 150 AND Vertical_Distance_To_Hydrology > 44 AND Horizontal_Distance_To_Roadways < 1237 AND (Hillshade_9am < 182 OR Hillshade_9am = 182) AND (Hillshade_Noon = 227 OR Hillshade_Noon > 227) AND (Hillshade_3pm = 164 OR Hillshade_3pm > 164) AND (Horizontal_Distance_To_Fire_Points = 1595 OR Horizontal_Distance_To_Fire_Points > 1595) 
 selectivity_result: 0.0


sql_query: SELECT COUNT(*) FROM dbms.forest WHERE (Elevation < 2907 OR Elevation = 2907) AND Slope > 21 AND Horizontal_Distance_To_Hydrology > 95 AND Vertical_Distance_To_Hydrology > 78 AND Horizontal_Distance_To_Roadways > 3045 AND (Hillshade_9am = 208 OR Hillshade_9am > 208) AND (Hillshade_Noon = 254 OR Hillshade_Noon > 254) AND Hillshade_3pm = 125 AND Horizontal_Distance_To_Fire_Points = 258 
 selectivity_result: 0.0


sql_query: SELECT COUNT(*) FROM dbms.forest WHERE Elevation > 3130 AND Slope < 20 AND Horizontal_

sql_query: SELECT COUNT(*) FROM dbms.forest WHERE Aspect = 113 AND (Slope = 13 OR Slope > 13) AND Horizontal_Distance_To_Hydrology < 90 AND Vertical_Distance_To_Hydrology = 82 AND (Horizontal_Distance_To_Roadways < 5501 OR Horizontal_Distance_To_Roadways = 5501) AND (Hillshade_9am < 251 OR Hillshade_9am = 251) AND (Hillshade_Noon = 218 OR Hillshade_Noon > 218) AND (Hillshade_3pm < 99 OR Hillshade_3pm = 99) AND Horizontal_Distance_To_Fire_Points < 1712 
 selectivity_result: 0.0


sql_query: SELECT COUNT(*) FROM dbms.forest WHERE (Aspect < 348 OR Aspect = 348) AND (Slope = 14 OR Slope > 14) AND (Horizontal_Distance_To_Hydrology < 90 OR Horizontal_Distance_To_Hydrology = 90) AND (Vertical_Distance_To_Hydrology = 5 OR Vertical_Distance_To_Hydrology > 5) AND Horizontal_Distance_To_Roadways = 1357 AND (Hillshade_9am < 232 OR Hillshade_9am = 232) AND (Hillshade_Noon < 237 OR Hillshade_Noon = 237) AND (Hillshade_3pm = 154 OR Hillshade_3pm > 154) AND (Horizontal_Distance_To_Fire_Points = 997 OR

sql_query: SELECT COUNT(*) FROM dbms.forest WHERE (Elevation = 3047 OR Elevation > 3047) AND (Aspect = 243 OR Aspect > 243) AND Slope < 16 AND Horizontal_Distance_To_Hydrology = 255 AND Vertical_Distance_To_Hydrology < 49 AND Horizontal_Distance_To_Roadways > 1595 AND (Hillshade_9am = 151 OR Hillshade_9am > 151) AND (Hillshade_Noon < 215 OR Hillshade_Noon = 215) AND Hillshade_3pm = 139 AND Horizontal_Distance_To_Fire_Points > 6207 
 selectivity_result: 0.0


sql_query: SELECT COUNT(*) FROM dbms.forest WHERE Elevation = 2934 AND (Aspect < 299 OR Aspect = 299) AND Slope > 7 AND (Horizontal_Distance_To_Hydrology = 85 OR Horizontal_Distance_To_Hydrology > 85) AND Vertical_Distance_To_Hydrology = 34 AND (Horizontal_Distance_To_Roadways < 1663 OR Horizontal_Distance_To_Roadways = 1663) AND Hillshade_9am < 214 AND Hillshade_Noon = 210 AND (Hillshade_3pm = 210 OR Hillshade_3pm > 210) AND Horizontal_Distance_To_Fire_Points < 1860 
 selectivity_result: 0.0


sql_query: SELECT COUNT(*) FROM dbms.

In [24]:

check_df.to_csv('selectivity_Data.csv', index=False)

# Testing

In [ ]:
# selected_rows = data.loc[0:4]

# # Iterate over each row and print column names and values vertically
# for index, row in selected_rows.iterrows():
#     print(f"Row {index}:")
#     for col in data.columns:
#         print(f"  {col}: {row[col]}")
#     print("\n")

In [ ]:
# # GENERATE THE QUERY FOR EACH ROW

# # Function to generate SQL query for each row in the DataFrame
# def generate_sql_query_with_or(df):
#     queries = []
#     for index, row in data.head(5).iterrows():
#         condition_dict = {}
#         for col in df.columns:
#             if '<' in col or '=' in col or '>' in col:
#                 attr, op = col.rsplit(' ', 1)
#                 if row[col] == 1:
#                     value_col = f"{attr} values"
#                     value = row[value_col]
#                     condition_str = f"{attr} {op} {value}"
#                     if attr in condition_dict:
#                         condition_dict[attr].append(condition_str)
#                     else:
#                         condition_dict[attr] = [condition_str]
        
#         # Forming conditions with 'OR' between the same attributes and 'AND' between different attributes
#         conditions = []
#         for attr, cond_list in condition_dict.items():
#             if len(cond_list) > 1:
#                 conditions.append(f"({' OR '.join(cond_list)})")
#             else:
#                 conditions.append(cond_list[0])
        
#         where_clause = ' AND '.join(conditions)
#         sql_query = f"SELECT COUNT(*) FROM DBMS.forest WHERE {where_clause}"
#         queries.append(sql_query)
     
#     return queries

# # Example usage with a sample DataFrame 'data'
# # Replace the placeholder with your actual DataFrame 'data'
# queries = generate_sql_query_with_or(data)
# for query in queries:
#     print(f"{query}\n\n")


In [ ]:
# generate the count of each query

import pandas as pd
import mysql.connector
from mysql.connector import Error

# Assuming 'connection' is your MySQL connection object

def execute_sql_queries_and_store_results(df):
    results = []  # List to store the results of each query
    for index, row in df.head(5).iterrows():
        condition_dict = {}
        for col in df.columns:
            if '<' in col or '=' in col or '>' in col:
                attr, op = col.rsplit(' ', 1)
                if row[col] == 1:
                    value_col = f"{attr} values"
                    value = row[value_col]
                    condition_str = f"{attr} {op} {value}"
                    if attr in condition_dict:
                        condition_dict[attr].append(condition_str)
                    else:
                        condition_dict[attr] = [condition_str]

        conditions = []
        for attr, cond_list in condition_dict.items():
            if len(cond_list) > 1:
                conditions.append(f"({' OR '.join(cond_list)})")
            else:
                conditions.append(cond_list[0])

        where_clause = ' AND '.join(conditions)
        sql_query = f"SELECT COUNT(*) FROM dbms.forest WHERE {where_clause}"

        # Execute the query
        try:
            cursor = connection.cursor()
            cursor.execute(sql_query)
            count_result = cursor.fetchone()[0]  # Assuming the query returns a single count value
            print(count_result)
            results.append(count_result)
        except Error as err:
            print("Error while executing query", err)
            results.append(None)  # Append None in case of an error
        finally:
            cursor.close()

    # Create a DataFrame from the results
    check_df = pd.DataFrame({'Result': results})
    return check_df

# Assuming 'data' is your DataFrame
check_df = execute_sql_queries_and_store_results(data)

# Display the resulting DataFrame
print(check_df)


In [ ]:
# selection = """
# select * from forest
# """

# results = read_query(connection, selection)
# for result in results:
#     print(result)